In [1]:
import matplotlib.pyplot as plt

import tensorflow as tf
from glob import glob
import pandas as pd
import os 
from tensorflow.keras.applications.inception_v3 import preprocess_input
from tensorflow.keras.preprocessing import sequence
import cv2 as cv
import numpy as np
import pickle

In [2]:
filesImages=os.listdir('./validation_data/flickr8k_validation_set_500_images')
path_models=os.listdir('./models')

In [3]:
print(filesImages)
print(path_models)

['captions.csv', 'Images']
['caption_model_v1.1.1_keras.keras', 'caption_model_v1_1_1.h5', 'InceptionEF_model.h5', 'vocab.pickle']


In [4]:
df=pd.read_csv(f"./validation_data/flickr8k_validation_set_500_images/{filesImages[filesImages.index('captions.csv')]}")

In [5]:
captions_image=df.groupby('image')['caption'].apply(list).to_dict()

In [6]:
captions_image

{'1007129816_e794419615.jpg': ['A man wears an orange hat and glasses .',
  'A man with glasses is wearing a beer can crocheted hat .',
  'A man with gauges and glasses is wearing a Blitz hat .',
  'The man with pierced ears is wearing glasses and an orange hat .',
  'A man in an orange hat starring at something .'],
 '1022454428_b6b660a67b.jpg': ['A couple with their newborn baby sitting under a tree facing a lake .',
  'Couple with a baby sit outdoors next to their stroller .',
  'A couple and an infant , being held by the male , sitting next to a pond with a near by stroller .',
  'A man and woman care for an infant along the side of a body of water .',
  'A couple sit on the grass with a baby and stroller .'],
 '103195344_5d2dc613a3.jpg': ['The man with the backpack is sitting in a buildings courtyard in front of an art sculpture reading .',
  'A man sitting in front of a metal sculpture in front of a building .',
  'A man sits and reads a newspaper by a sculpture outside of an off

In [7]:
images_test=glob('./validation_data/flickr8k_validation_set_500_images/Images/*.jpg')

In [8]:
list_of_images_path = list(captions_image.keys())

In [9]:
list_of_images_path

['1007129816_e794419615.jpg',
 '1022454428_b6b660a67b.jpg',
 '103195344_5d2dc613a3.jpg',
 '1072153132_53d2bb1b60.jpg',
 '1075881101_d55c46bece.jpg',
 '109260216_85b0be5378.jpg',
 '1100214449_d10861e633.jpg',
 '1130369873_d80a1aa59c.jpg',
 '1177994172_10d143cb8d.jpg',
 '1204996216_71d7519d9a.jpg',
 '1247181182_35cabd76f3.jpg',
 '1255504166_f2437febcb.jpg',
 '1287073593_f3d2a62455.jpg',
 '129599450_cab4e77343.jpg',
 '1298295313_db1f4c6522.jpg',
 '1299459550_1fd5594fa2.jpg',
 '1350811702_2ce7cfd0c5.jpg',
 '1368383637_614646cc4a.jpg',
 '1389264266_8170bc1c54.jpg',
 '1396064003_3fd949c9dd.jpg',
 '141140165_9002a04f19.jpg',
 '1414820925_3504c394e1.jpg',
 '1428641354_f7453afbea.jpg',
 '143552697_af27e9acf5.jpg',
 '143688283_a96ded20f1.jpg',
 '1439282131_3814d6ae04.jpg',
 '1446933195_8fe9725d62.jpg',
 '1452361926_6d8c535e32.jpg',
 '1453366750_6e8cf601bf.jpg',
 '1454841725_4b6e6199e2.jpg',
 '1461667284_041c8a2475.jpg',
 '1463732807_0cdf4f22c7.jpg',
 '1472653060_7427d2865a.jpg',
 '1473618073_7db

In [10]:
def proprocessing(imge):
    img_read=plt.imread(imge)
    img=cv.resize(img_read,(299,299))
    img=preprocess_input(img)
    return np.array(img)

In [11]:
with open('./models/vocab.pickle','rb') as f:
    tokenizer=pickle.load(f)

In [12]:
def beam_search(model_cnn,model_rnn,image,beam_size=3):
    images=proprocessing(image)
    dim=np.expand_dims(images,0)
    cnn_model=model_cnn.predict(dim,verbose=1)
    sequnce=[[['startseq'],0.0]]
    for _ in range(40):
        all_condidates=[]
        for seq,score in sequnce:
            if seq[-1]=='endseq':
                all_condidates.append((seq,score))
                continue
            encoder=tokenizer.texts_to_sequences([' '.join(seq)])
            encoder=sequence.pad_sequences(encoder,maxlen=40,padding='post')
            rnn_model=model_rnn.predict([cnn_model,encoder],verbose=0)[0]
            top_k=np.argsort(rnn_model)[-beam_size:]
            for word_indx in top_k:
                word=tokenizer.index_word.get(word_indx)
                if word is None :
                    continue 
                condidate=seq+[word]
                candidate_score = score - np.log(rnn_model[word_indx] + 1e-9)
                all_condidates.append((condidate,candidate_score))
        sequnce=sorted(all_condidates,key=lambda x:x[1])[:beam_size]

    return ' '.join(sequnce[0][0])
                                
    
    

In [13]:
from tensorflow.keras.models import load_model

In [14]:
rnn,cnn=load_model('./models/caption_model_v1_1_1.h5'),load_model('./models/InceptionEF_model.h5')

In [25]:
import random 
import textwrap
%matplotlib inline
pthing='./validation_data/flickr8k_validation_set_500_images/Images/'
random.shuffle(list_of_images_path)
ax,fig=plt.subplots(3,3,figsize=(20,20))
flatten=fig.flatten()
for i,k in enumerate(flatten):
    pred=beam_search(cnn,rnn,pthing+list_of_images_path[i],10)
    caption='\n'.join(textwrap.wrap(pred,width=30))
    read=plt.imread(pthing+list_of_images_path[i])
    resize=cv.resize(read,(299,299))
    k.imshow(resize)
    k.set_title(caption)
plt.show()


1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 279ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 267ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 493ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 294ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 1s 602ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 259ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 350ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 406ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 285ms/step


<Figure size 640x480 with 0 Axes>

In [16]:
from tensorflow.keras.utils import plot_model

In [ ]:
# plot_model(cnn,to_file='./cnn_archt.png',show_shapes=True,show_layer_names=True)

In [18]:
# !apt-get install -y graphviz
# !pip install pydot

In [19]:
# If you are using Anaconda/Miniconda (Highly Recommended)
# !conda install -c conda-forge python-graphviz -y

# IF YOU ARE NOT USING CONDA, use these instead:
# !pip install pydot
# !pip install graphviz

In [20]:
print('hello')

hello
